# FLASH Workflow

Let's say we want to build a simulation of a sphere of constant density undergoing gravitational collapse. We create the directory that contains all the simulation code stored in ``source/Simulation/SimulationMain/UniformSphere``.

These are the neceesary files for the Simulation module (in the order of most to least commonly modified) that should be in that directory: 

- __flash.par__: contains the parameters used in the simulation. Technically, you could just write the numerical values of these variables in the F90 code, but flash.par is useful when you just want to make quick changes to the parameters to see what happens without having to recompile the code. For example, if I want to simulate a sphere, I might want to leave its density and radius as a variables in flash.par.

- __Simulation_initBlock.F90__: specifies how the initial condition should be set up. (More on this in the next tutorial)    
- __Simulation_init.F90__: 
    Simulation init routine will get the necessary runtime parameters and store them in the Simulation data Fortran module, and also initialize other variables in the module. You can think of this as the code that goes at the top of your Fortran code (#include header files, variable declaration ..).
    
    Here's a basic template for Simulation_init():
    ~~~fortran
      subroutine Simulation_init()

      use Simulation_data
      use Driver_interface, ONLY : Driver_getMype, Driver_abortFlash
      use RuntimeParameters_interface, ONLY : RuntimeParameters_get
      use Logfile_interface, ONLY : Logfile_stamp
      implicit none
      #include "constants.h"
      #include "Flash.h"

      integer :: myPE, pno, blockID
      real    :: pt
      logical :: restart

      ! do nothing on restart
      call RuntimeParameters_get("restart", restart)

      call Driver_getMype(GLOBAL_COMM, myPE)
      sim_globalMe = myPE
      
      ! Get Runtime Parameters
      call RuntimeParameters_get('beta_param',beta_param) !rotation beta
      call RuntimeParameters_get('gamma', sim_gamma)
      call RuntimeParameters_get('alpha',alpha) ! thermal-to-magnetic pressure ratio
      call Logfile_stamp( "initializing UniformSphere problem",  &
           "[Simulation_init]")
      
     ~~~
For example, ``call RuntimeParameters_get('gamma', sim_gamma)`` to read in the 'gamma' parameter in flash.par into the Fortran variable ``sim_gamma``
- __Simulation_data.F90__: tells FLASH which variables to store.
    ~~~fortran
    module Simulation_data
      implicit none
      !! Runtime Parameters
      real, save :: beta_param,sim_gamma,alpha
    end module Simulation_data
    ~~~
- __Config__: Specifies what types of modules (Sink, MHD, radiation ..etc) you will be loading in for your simulation.
    - ``REQUIRES`` specify which modules you need. Generally for Hydro problems, you need:
        ~~~fortran
        REQUIRES Driver
        REQUIRES physics/Eos/EosMain/Gamma
        REQUIRES physics/Hydro
        ~~~
    - ``PARAMETER`` lists all the runtime parameters specific to the problem. You can define a value for these variables in the Config or override these default values in ``flash.par``
        ~~~fortran
        PARAMETER sim_dens    REAL    1.1E-19
        ~~~
- __Makefile__ : Usually you don't touch this.

An example of the UniformSphere problem setup is in **FILELOC**.

# Compile and run

After finishing setting up the problem in these files, it is time to compile your simulation modules.

###### 1) Load in hdf5 modules (put this inside your .bashrc):  
    module load cray-hdf5-parallel/1.8.11
##### 2) Setup copies all the code necessary for the simulation into the object/ directory.
Note that whatever settings you put in ./setup will override what you put in Config.   

    ./setup UniformSphere -3d --maxblock=500  -auto

The syntax for running ``setup`` is as follows:
    
    ./setup <problem-name> [options] [VAR=VALUE]
    
Here are some setup parameters that I think is important: 
    
- **-3d** : 3D simulation, otherwise default is -2d. 
   
- **+usm**: Unsplit Staggered Mesh Solver : use this with sink particles, doesn't work very well with MHD.    
   
- **--maxblock ** : The maximum number of blocks per processor. FLASH will try to allocate enough memory upon initialization for this many blocks, so its better to keep this number low <500, but it depends on the simulation and the number of cores that you are using. 
- **-auto**: A "catch-all" flag that sets up the problem the way FLASH think it should be setup, this can be dangerous and you should always check the top of the object/*.log file after you start the simulation, to check that the setup parameters correspond to what you think should be loaded.

For a detailed list of things that you could input into setup, enter ``./setup -h``.

###### 3) Compile the code in object/
   
   
make -j <num-proc> : Running make in parallel to compile the code into the object/ directory 

All in one line : ``./setup UniformSphere -3d --maxblock=500  -auto ; cd object/;make -j8;cd ..;``